In [1]:
import pandas as pd
import numpy as np
import re
!pip install openpyxl

import warnings
warnings.filterwarnings("ignore")

In [2]:
#intialize a dictionary for all the tables as keys and information we extract from each 
#table as its value
#IMS is International migrant stock
#RMS refugee migrant stock

dict_ = {'Table 1' : 'IMS' , 
         'Table 2' : 'total_population', 
         'Table 3' : 'IMS_total_population' , 
         'Table 4' : 'female_IMS', 
         'Table 5' : 'IMS_ROC' , 
         'Table 6' : ['RMS' , 'RMS_IMS','RMS_ROC']}

In [3]:
def get_annex(df):
    #annex = pd.read_excel(io="UN_MigrantStockTotal_2015.xlsx", sheet_name= "ANNEX" , index_col=False)
    df.drop(df.index[0:14] , inplace = True)
    df.drop(columns={'Unnamed: 2' , 'Unnamed: 5', 'Unnamed: 8'} , inplace = True)
    df.rename({'Unnamed: 0' : 'country_code' , 
              'Unnamed: 1' : 'country' ,
              'Unnamed: 3' : 'major_area',
              'Unnamed: 4' : 'major_area_code',
              'Unnamed: 6' : 'region',
              'Unnamed: 7' : 'region_code',
              'Unnamed: 9' : 'developed_region',
              'Unnamed: 10' : 'least_developed_country',
              'Unnamed: 11' : 'sub_saharan_africa'}, axis = 'columns' , inplace = True)
    df.reset_index(drop = True , inplace = True)
    return df

In [4]:
def get_data_type(df):
    df.drop(df.index[0:23] , inplace = True)
    df.rename({'Unnamed: 3' : 'country_code' , 'Unnamed: 4' : 'type_of_data'} , axis = 'columns' , inplace = True)
    df1 = df[['country_code' , 'type_of_data']]
    df1['foreign_pop_status']  = df1.type_of_data.str.extract(pat = '(B|C)')
    df1['refugee_incl']  = df1.type_of_data.str.extract(pat = '(R)')
    df1['imputation']  = df1.type_of_data.str.extract(pat = '(I)')
    df1.replace({'foreign_pop_status' : {'B' : 'born' , 'C' : 'citizen'}}, inplace = True) 
    df1.replace({'refugee_incl' : {'R' : 'yes' , np.nan : 'no'}}, inplace = True)
    df1.replace({'imputation' : {'I' : 'yes' , np.nan : 'no'}} , inplace = True)
    df1.drop(columns = 'type_of_data' , inplace = True)
    df1.reset_index(drop = True , inplace = True)
    return df1

In [5]:
#define a function to rename columns as it is a repetitive task
#all columns are named as 1,2,3.. when we load dataframe in python so 'i' is the starting value
#loop will start from column 'i'

def rename_columns(df1):
    #label read the value from df where the column header from excel file is stored
    label = df1.iloc[0][df1.columns[1]]
    
    #loop starting from second column till end because we dont want to rename country code
    lst = list(df1.columns[1:len(df1.columns)])
    
    for each in lst:
        #condition to check if first index(column header) is still the same
        #when value at 0 index changes label will be updated with the new value
        if(pd.notnull(df1.iloc[0][each])):
            label = df1.iloc[0][each]
       
        #code to rename column
        df1.rename({each : str(df1.iloc[1][each])+str(label).lower()} , axis = 'columns' , inplace = True)

    return df1


In [49]:
#funtion to clean table

def clean_table(df , key): 
    #remove first 13 rows as the contain the header of the table and lots of nan values
    df.drop(df.index[0:13] , inplace = True)
    
    #rename 3rd column as country code
    df.rename({'Unnamed: 3' : 'country_code' }, axis = 'columns' , inplace = True)
   
    #drop sort order, notes and type of data columns
    df.drop(columns=['Unnamed: 0' , 'Unnamed: 1' , 'Unnamed: 2'] , inplace = True)
    
    #condition because table 2 does not have type of data so we need to skip for table 2
    if(key!=dict_['Table 2']):
        df.drop(columns=['Unnamed: 4'] , inplace = True)
        
    #function call to rename rest of the columns
    df = rename_columns(df)
    
    #drop top 9 rows till sub-saharan africa as it is just summary data which can be easily
    #derived through simple code in python
    #df.drop(df.index[0:7] , inplace = True)
    
    #use melt function to change orientation of data
    #two new columns will be formed tmp will contain all the column headers
    #key value that we stored in dict_ will form the other columns
   
    df_v1 = pd.melt(df, id_vars = 'country_code', 
                    value_vars = list(df.columns[1:len(df.columns)]), 
                    var_name = "tmp" , 
                    value_name = key)
   
    #check for missing values
    df_v1['tmp'].replace('..', np.nan, inplace=True)
    
    #extract year from tmp column
    df_v1['year']  = df_v1.tmp.str.extract(pat = '([0-9-]+)')
    
    #extract sex from tmp column
    df_v1['sex']  = df_v1.tmp.str.extract(pat = '(?i)(both|male|female)')
    
    #drop tmp as useful info has been obtained
    df_v1.drop(columns = "tmp" , inplace = True)
    df_v1.reset_index()
    return df_v1


In [67]:
#main table
df2 = pd.DataFrame()

#rate of change dataframe
df3 = pd.DataFrame()
lst_ = []
flag = False

for key in dict_:
    df = pd.read_excel(io="UN_MigrantStockTotal_2015.xlsx", sheet_name= key , index_col=False)
    
    if(key == 'Table 6'):
        df1 = clean_table(df[list(df.columns[0:10])].copy(), dict_[key][0])
        df2 = pd.merge(df2,df1 , on = ['country_code' , 'year' , 'sex'], how = 'left')
       
        df1 = clean_table(df[list(df.columns[[0,1,2,3,4,11,12,13,14,15,16]])].copy() , dict_[key][1])
        df2 = pd.merge(df2,df1 , on = ['country_code' , 'year'], how = 'left').drop(columns = ['sex_y'])
        
        df1 = clean_table(df[list(df.columns[[0,1,2,3,4,17,18,19,20,21]])].copy() , dict_[key][2])
        flag = True
   
    else:
        df1 = clean_table(df , dict_[key])
    
    #list of all tables
    lst_.append(df1)
    
    #add IMS_ROC to df3
    if(key == 'Table 5'):
        flag = True
        
    #join tables
    if (flag != True):
        if(df2.empty):
            df2 = df1
        else:
            if(key != 'Table 4'):
                df2 = pd.merge(df2,df1 , on = ['country_code' , 'year' , 'sex'], how = 'outer')
            else:
                df2 = pd.merge(df2,df1 , on = ['country_code' , 'year' , 'sex'], how = 'outer')
    else:
        if(df3.empty): 
            df3 = df1
            flag = False
        else:
            df3 = pd.merge(df3,df1, on = ['country_code' , 'year'], how = 'left').drop(columns = ['sex_y'])
            df3.rename({'sex_x' : 'sex'} , axis = 'columns', inplace = True)
            flag = False
    df2.rename({'sex_x' : 'sex'} , axis = 'columns', inplace = True)
    

#print(df2.groupby(by = ['country_code' , 'year' , 'sex']).size().head(50))


#join all table with annex
annex = (get_annex(pd.read_excel(io="UN_MigrantStockTotal_2015.xlsx", sheet_name= 'ANNEX' , index_col=False)))
tmp = pd.merge(annex,df2, on = 'country_code' , how = 'left')

#join with datatype
datatype = get_data_type(pd.read_excel(io="UN_MigrantStockTotal_2015.xlsx", sheet_name= "Table 1" , index_col=False))

#make one column for underdeveloped and developed
final_table = pd.merge(tmp, datatype, on = 'country_code' , how = 'left')
final_table.replace({'developed_region' : {'Yes' : 'more' , 'No' : 'less'}}, inplace = True) 
final_table.replace({'least_developed_country' : {'Yes' : 'least' , 'No' : 'less'}}, inplace = True) 
final_table['country_classification'] = final_table['developed_region'] + final_table['least_developed_country']
final_table['country_classification'].replace('lessleast', 'least', inplace=True)
final_table['country_classification'].replace('moreless', 'more', inplace=True)
final_table['country_classification'].replace('lessless', 'less', inplace=True)
final_table.drop(columns = ['developed_region' , 'least_developed_country'] , inplace = True)


final_roc = pd.merge(annex, df3, on = 'country_code' , how = 'left')
final_roc.drop(columns = ['country', 'major_area', 'major_area_code', 'region', 'region_code', 'developed_region','least_developed_country', 'sub_saharan_africa'] , inplace = True)

print(display(final_roc))
print(display(final_table))
#print(final_table['population_citz_status'].unique())

country_code   IMS_ROC       year     sex     RMS_ROC
0               4  4.299812  1990-1995    both   128.99347
1               4  1.192711  1995-2000    both          ..
2               4  2.794196  2000-2005    both          ..
3               4  3.160624  2005-2010    both  102.911692
4               4  26.37988  2010-2015    both   50.501739
...           ...       ...        ...     ...         ...
3475          716 -7.890123  1990-1995  female -110.036176
3476          716 -0.998071  1995-2000  female   42.669158
3477          716 -0.867001  2000-2005  female    2.304118
3478          716  0.259214  2005-2010  female   -0.262999
3479          716  0.065769  2010-2015  female    3.877364

[3480 rows x 5 columns]

None


country_code      country major_area major_area_code          region  \
0               4  Afghanistan       Asia             935   Southern Asia   
1               4  Afghanistan       Asia             935   Southern Asia   
2               4  Afghanistan       Asia             935   Southern Asia   
3               4  Afghanistan       Asia             935   Southern Asia   
4               4  Afghanistan       Asia             935   Southern Asia   
...           ...          ...        ...             ...             ...   
4171          716     Zimbabwe     Africa             903  Eastern Africa   
4172          716     Zimbabwe     Africa             903  Eastern Africa   
4173          716     Zimbabwe     Africa             903  Eastern Africa   
4174          716     Zimbabwe     Africa             903  Eastern Africa   
4175          716     Zimbabwe     Africa             903  Eastern Africa   

     region_code sub_saharan_africa       IMS  year     sex total_population  \
0           5501                 No     57686  1990    both         12067.57   
1           5501                 No     71522  1995    both        16772.522   
2           5501                 No     75917  2000    both         19701.94   
3           5501                 No     87300  2005    both        24399.948   
4           5501                 No  102246.0  2010    both        27962.207   
...          ...                ...       ...   ...     ...              ...   
4171         910                Yes    185214  1995  female         5877.504   
4172         910                Yes    176198  2000  female         6280.133   
4173         910                Yes    168723  2005  female          6548.18   
4174         910                Yes  170924.0  2010  female         7068.861   
4175         910                Yes  171487.0  2015  female         7915.194   

     IMS_total_population female_IMS     RMS    RMS_IMS foreign_pop_status  \
0                0.478025        NaN      25   0.043338               born   
1                0.426424        NaN   19605  27.411146               born   
2                0.385328        NaN       0          0               born   
3                0.357788        NaN      32   0.036655               born   
4                0.365658        NaN  6434.0   6.292667               born   
...                   ...        ...     ...        ...                ...   
4171             3.151236  42.950564     NaN   0.119195               born   
4172             2.805641  42.970825     NaN   1.006485               born   
4173              2.57664  42.965625     NaN   1.129381               born   
4174             2.417985  42.957493     NaN   1.114627               born   
4175             2.166555  42.993637     NaN   1.353086               born   

     refugee_incl imputation country_classification  
0              no         no                  least  
1              no         no                  least  
2              no         no                  least  
3              no         no                  least  
4              no         no                  least  
...           ...        ...                    ...  
4171          yes         no                   less  
4172          yes         no                   less  
4173          yes         no                   less  
4174          yes         no                   less  
4175          yes         no                   less  

[4176 rows x 19 columns]

None


In [8]:
#Read notes
notes = pd.read_excel(io="UN_MigrantStockTotal_2015.xlsx", sheet_name= "NOTES" , index_col=False)
notes.drop(notes.index[0:14] , inplace = True)
notes.rename(columns={"Unnamed: 0": "code", "Unnamed: 1": "notes"} , inplace = True)
notes.set_index('code', inplace=True)
print(display(notes))

notes
code                                                   
(a)   The column labeled “Type of data” indicates wh...
(b)   More developed regions comprise Europe, Northe...
(c)   Less developed regions comprise all regions of...
(d)   The least developed countries, as defined by t...
(e)   Sub-Saharan Africa refers to all of Africa exc...
(1)     Including Agalega, Rodrigues and Saint Brandon.
(2)                                 Including Zanzibar.
(3)   The estimates for 1990 to 2005 refer to Sudan ...
(4)           Including Ascension and Tristan da Cunha.
(5)   For statistical purposes, the data for China d...
(6)   As of 1 July 1997, Hong Kong became a Special ...
(7)   As of 20 December 1999, Macao became a Special...
(8)                        Including Sabah and Sarawak.
(9)                         Including Nagorno-Karabakh.
(10)                         Including Northern-Cyprus.
(11)              Including Abkhazia and South Ossetia.
(12)  Including East Jerusalem. Refugees are not par...
(13)                            Including Transnistria.
(14)                    Refers to Guernsey, and Jersey.
(15)                           Including Åland Islands.
(16)          Including Svalbard and Jan Mayen Islands.
(17)                  Refers to the Vatican City State.
(18)  Including Kosovo. The estimates for 1990 and 2...
(19)       Including Canary Islands, Ceuta and Melilla.
(20)  The estimates for 1990 to 2005 refer to the fo...
(21)  Including Saint-Barthélemy and Saint-Martin (F...
(22)  Including Christmas Island, Cocos (Keeling) Is...

None


In [9]:
for each in lst_: 
    print(display(each))

country_code                                                IMS  year  \
0     Country code  International migrant stock at mid-year (both ...  1990   
1              NaN                                               1990  1990   
2              900                                          152563212  1990   
3              901                                           82378628  1990   
4              902                                           70184584  1990   
...            ...                                                ...   ...   
4801           882                                             2460.0  2015   
4802           772                                              254.0  2015   
4803           776                                             2604.0  2015   
4804           798                                               63.0  2015   
4805           876                                             1411.0  2015   

         sex  
0       both  
1       both  
2       both  
3       both  
4       both  
...      ...  
4801  female  
4802  female  
4803  female  
4804  female  
4805  female  

[4806 rows x 4 columns]

None


country_code                                   total_population  year  \
0     Country code  Total population of both sexes at mid-year (th...  1990   
1              NaN                                               1990  1990   
2              900                                        5309667.699  1990   
3              901                                        1144463.062  1990   
4              902                                        4165204.637  1990   
...            ...                                                ...   ...   
4801           882                                             93.584  2015   
4802           772                                                 ..  2015   
4803           776                                             52.931  2015   
4804           798                                                 ..  2015   
4805           876                                                 ..  2015   

         sex  
0       both  
1       both  
2       both  
3       both  
4       both  
...      ...  
4801  female  
4802  female  
4803  female  
4804  female  
4805  female  

[4806 rows x 4 columns]

None


country_code                               IMS_total_population  year  \
0     Country code  International migrant stock as a percentage of...  1990   
1              NaN                                               1990  1990   
2              900                                            2.87331  1990   
3              901                                           7.198015  1990   
4              902                                           1.685021  1990   
...            ...                                                ...   ...   
4801           882                                           2.628654  2015   
4802           772                                                 ..  2015   
4803           776                                           4.919612  2015   
4804           798                                                 ..  2015   
4805           876                                                 ..  2015   

         sex  
0       both  
1       both  
2       both  
3       both  
4       both  
...      ...  
4801  female  
4802  female  
4803  female  
4804  female  
4805  female  

[4806 rows x 4 columns]

...

None


country_code                                            IMS_ROC  \
0     Country code  Annual rate of change of the migrant stock (bo...   
1              NaN                                          1990-1995   
2              900                                           1.051865   
3              901                                           2.275847   
4              902                                          -0.487389   
...            ...                                                ...   
4000           882                                          -0.545343   
4001           772                                            2.60325   
4002           776                                           2.526318   
4003           798                                          -1.819436   
4004           876                                           0.516899   

           year     sex  
0     1990-1995    both  
1     1990-1995    both  
2     1990-1995    both  
3     1990-1995    both  
4     1990-1995    both  
...         ...     ...  
4000  2010-2015  female  
4001  2010-2015  female  
4002  2010-2015  female  
4003  2010-2015  female  
4004  2010-2015  female  

[4005 rows x 4 columns]

None


country_code                                     RMS_ROC       year  sex
0     Country code  Annual rate of change of the refugee stock  1990-1995  NaN
1              NaN                                   1990-1995  1990-1995  NaN
2              900                                   -2.123497  1990-1995  NaN
3              901                                    9.388424  1990-1995  NaN
4              902                                   -2.839417  1990-1995  NaN
...            ...                                         ...        ...  ...
1330           882                                          ..  2010-2015  NaN
1331           772                                          ..  2010-2015  NaN
1332           776                                          ..  2010-2015  NaN
1333           798                                          ..  2010-2015  NaN
1334           876                                          ..  2010-2015  NaN

[1335 rows x 4 columns]

None


In [69]:
#Do not run this code it will legit take 5 mins and system would also stuck
#but could also work if you wanna see each row


with pd.option_context('display.max_rows', None, 'display.max_columns', None):  # more options can be specified also
    #print(display(final_table))

country_code                                            country  \
0               4                                        Afghanistan   
1               4                                        Afghanistan   
2               4                                        Afghanistan   
3               4                                        Afghanistan   
4               4                                        Afghanistan   
5               4                                        Afghanistan   
6               4                                        Afghanistan   
7               4                                        Afghanistan   
8               4                                        Afghanistan   
9               4                                        Afghanistan   
10              4                                        Afghanistan   
11              4                                        Afghanistan   
12              4                                        Afghanistan   
13              4                                        Afghanistan   
14              4                                        Afghanistan   
15              4                                        Afghanistan   
16              4                                        Afghanistan   
17              4                                        Afghanistan   
18              8                                            Albania   
19              8                                            Albania   
20              8                                            Albania   
21              8                                            Albania   
22              8                                            Albania   
23              8                                            Albania   
24              8                                            Albania   
25              8                                            Albania   
26              8                                            Albania   
27              8                                            Albania   
28              8                                            Albania   
29              8                                            Albania   
30              8                                            Albania   
31              8                                            Albania   
32              8                                            Albania   
33              8                                            Albania   
34              8                                            Albania   
35              8                                            Albania   
36             12                                            Algeria   
37             12                                            Algeria   
38             12                                            Algeria   
39             12                                            Algeria   
40             12                                            Algeria   
41             12                                            Algeria   
42             12                                            Algeria   
43             12                                            Algeria   
44             12                                            Algeria   
45             12                                            Algeria   
46             12                                            Algeria   
47             12                                            Algeria   
48             12                                            Algeria   
49             12                                            Algeria   
50             12                                            Algeria   
51             12                                            Algeria   
52             12                                            Algeria   
53             12                                            Algeria   
54             16                            

None
